In [1]:
paths.dir("./")

{
  1 : ..
  2 : Code
  3 : .
  4 : DQN_Batch_CNN.ipynb
  5 : data
  6 : .gitignore
  7 : .git
  8 : Presentation
  9 : README.md
  10 : .ipynb_checkpoints
  11 : Paper
}


In [2]:
require 'os'
require 'nn'
require 'rnn'
require 'optim'
-- require 'cunn'
-- require 'cunnx'
-- require 'cutorch'
require 'parallel'

dl = require 'dataload'

In [3]:
dofile("Code/utils.lua")
dofile("Code/utilsNNbatch.lua")
dofile("Code/Utils/load_cnn.lua")

...Utils file loaded	


...Utils file loaded	


In [4]:
outputpath = '/home/francisco/GitHub/DQN-Event-Summarization/data/training/'

In [5]:
torch.setnumthreads(torch.getnumthreads())

In [9]:
i = 0
path = '/home/francisco/GitHub/DQN-Event-Summarization/data/training/'
queries, sentences, trueSummary  = {}, {}, {}
queries[i + 1 ] = torch.load(path .. string.format("qtokens_sid_%i.dat", i))
sentences[i + 1] = torch.load(path .. string.format("stokens_sid_%i.dat", i))
trueSummary[i + 1] = torch.load(path .. string.format("tstokens_sid_%i.dat", i))

In [10]:
n = 500

In [15]:
print(queries[1]:size(), sentences[1]:size(), trueSummary[1]:size())

 85194
    19
[torch.LongStorage of size 2]

 85194
   662
[torch.LongStorage of size 2]

 85194
  1154
[torch.LongStorage of size 2]



In [ ]:
function loadCNN(path, n)
    local queries, sentences, trueSummary  = {}, {}, {}
    for i = 0, 124 do
        queries[i + 1 ] = torch.load(path .. string.format("qtokens_sid_%i.dat", i))
        sentences[i + 1] = torch.load(path .. string.format("stokens_sid_%i.dat", i))
        trueSummary[i + 1] = torch.load(path .. string.format("tstokens_sid_%i.dat", i))
        if n ~= nil then 
            if n < queries[i + 1]:size(1) then 
                queries[i + 1] = queries[i + 1][{{1, n}}]
                sentences[i + 1] = sentences[i + 1][{{1, n}}]
                trueSummary[i + 1] = trueSummary[i + 1][{{1, n}}]
            end
        end
    end
    return queries, sentences, trueSummary
end

outputpath = '/home/francisco/GitHub/DQN-Event-Summarization/data/training/'

In [6]:
queries, sentences, trueSummaries = loadCNN(outputpath, 500)

In [7]:
vocab_size = 20001
learning_rate=1e-5
embDim = 50
gamma=0
batch_size = 25
mem_multiplier = 1
cuts = 4
endexplorerate=0.8
base_explore_rate=0.1
nepochs = 100
epsilon = 1
print_perf=false
adapt=false
adapt_lambda = 0.25
usecuda= false
seedval= 420

In [8]:
if usecuda then
    Tensor = torch.CudaTensor
    LongTensor = torch.CudaLongTensor   
    ByteTensor = torch.CudaByteTensor
    maskLayer = nn.MaskedSelect():cuda()
    print("...running on GPU")
else
    Tensor = torch.Tensor
    LongTensor = torch.LongTensor
    ByteTensor = torch.ByteTensor
    maskLayer = nn.MaskedSelect()
    print("...running on CPU")
end

...running on CPU	


In [9]:
SKIP = 1
SELECT = 2

k = sentences[1]:size(2)
n = queries[1]:size(1)
q = queries[1]:size(2)
n_s = #queries

optimParams = { learningRate = learning_rate }
delta = cuts / nepochs
end_baserate = torch.round(nepochs * endexplorerate )


qTokens = {}
for i=1, n do
    qTokens[i] = Tokenize({trueSummaries[1][i]:totable()}, false)[1]
end

-- Building the model
model = buildModel('bow', vocab_size, embDim, 'f1', adapt, usecuda)
params, gradParams = model:getParameters()

if adapt then 
    criterion = nn.ParallelCriterion():add(nn.MSECriterion()):add(nn.BCECriterion())
    criterion["weights"] = {1, adapt_lambda}
else 
    criterion = nn.MSECriterion()
end 


Running bag-of-words model to learn f1	


In [10]:
vocabsize = 0
for i=1, 124 do
    vocabsize = math.max(queries[i]:max(), sentences[i]:max(), trueSummaries[i]:max(), vocabsize)
end

In [11]:
print(string.format("Running model with %i queries and %i sentences", n, n_s))
qValues = {}
qActions = {}
qPreds = {}
rewards = {}
lossfull = {}
rouguef1 = {}
rougue_scores = {}

totalPredsummary = LongTensor(n, n_s * k):fill(0)

memfull = false
curr_memsize = 0
memsize = n * n_s * mem_multiplier
queryMemory = Tensor(memsize, q):fill(0)
qActionMemory = Tensor(memsize, 2):fill(0)
predSummaryMemory = Tensor(memsize, n_s * k):fill(0)
sentenceMemory = Tensor(memsize, k):fill(0)
sentencetp1Memory  = Tensor(memsize, k):fill(0)
predSummarytp1Memory = Tensor(memsize, n_s * k):fill(0)
qPredsMemory = Tensor(memsize, 2):fill(0)
qValuesMemory = Tensor(memsize, 1):fill(0)
rewardMemory = Tensor(memsize, 1):fill(0)
totalPreds = Tensor(n, 2):fill(0)


Running model with 500 queries and 125 sentences	


$ Torch: not enough memory: you tried to allocate 38GB. Buy new RAM! at /tmp/luarocks_torch-scm-1-9784/torch7/lib/TH/THGeneral.c:270
stack traceback:
	[C]: at 0x7f1d74ca5320
	[C]: in function 'Tensor'
	[string "print(string.format("Running model with %i qu..."]:17: in main chunk
	[C]: in function 'xpcall'
	/home/francisco/torch/install/share/lua/5.1/itorch/main.lua:210: in function </home/francisco/torch/install/share/lua/5.1/itorch/main.lua:174>
	/home/francisco/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	...francisco/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	...francisco/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	...francisco/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/home/francisco/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x00405d50: 

In [53]:
for i = 1, n_s do
    qPreds[i] = Tensor(n, 2):fill(0) 
    qValues[i] = Tensor(n, 1):fill(0)
    qActions[i] = Tensor(n, 2):fill(0)
    rewards[i] = Tensor(n, 1):fill(0)
    rougue_scores[i] = Tensor(n, 1):fill(0)
    if adapt then
        regPreds[i] = Tensor(n, 1):fill(0)
    end        
end 

In [54]:
for i=1, n_s do
    qPreds[i]:fill(0)
    qValues[i]:fill(0)
    qActions[i]:fill(0)
    rewards[i]:fill(0)
    rougue_scores[i]:fill(0)
    totalPredsummary:fill(0)
    if adapt then
        regMemory[i]:fill(0)
    end        
end

In [55]:
i = 1

In [56]:
totalPreds:fill(0)
start_row = 1
end_row = batch_size
c = 1             
for start_row=1, n, batch_size do                 
    end_row = c * batch_size

    if end_row > n then 
        end_row = n
    end
    totalPreds[{{start_row, end_row}}]:copy(
        model:forward({
            queries[i][{{start_row, end_row}}], 
            sentences[i][{{start_row, end_row}}], 
            totalPredsummary[{{start_row, end_row}}]
        })
    )
    c = c + 1
end


In [58]:
if adapt then 
    qPreds[i]:copy(totalPreds[1])
    regPreds[i]:copy(totalPreds[2])
else
    qPreds[i]:copy(totalPreds)
end

In [59]:
if torch.uniform(0, 1) <= epsilon then
    -- randomly choosing actions
    xrand = torch.rand(qPreds[i]:size())
    qActions[i]:select(2, SELECT):copy(torch.ge(xrand:select(2, SELECT), xrand:select(2, SKIP)))
    qActions[i]:select(2, SKIP):copy(torch.ge(xrand:select(2, SKIP), xrand:select(2, SELECT)))
    qValues[i]:copy( maskLayer:forward({totalPreds, qActions[i]:byte()}) )
else 
    qMax, qindx = torch.max(qPreds[i], 2)  -- Pulling the best actions
    -- Here's the fast way to select the optimal action for each query
    qActions[i]:copy(
        qActions[i]:scatter(2, qindx, torch.ones(qPreds[i]:size())):clone()
    )
    qValues[i]:copy(
        qMax
    )
end

In [62]:
start_row = curr_memsize + 1
if memsize < (start_row + n) then 
    start_row = memsize - n + 1
    end_row = start_row + n - 1
    curr_memsize = 0
    if (end_row + n) >= memsize then 
        memfull = true
    end 
else 
    end_row = start_row + n - 1
    curr_memsize = end_row
end

In [80]:
-- Update memory sequentially until it's full then restart updating it
queryMemory[{{start_row, end_row}}]:copy(queries[i])
print()

In [86]:
sentenceMemory:size()

 62500
   125
[torch.LongStorage of size 2]



In [1]:
sentenceMemory[{{start_row, end_row}}]:copy(sentences[i])
print()

[string "sentenceMemory[{{start_row, end_row}}]:copy(s..."]:1: attempt to index global 'sentenceMemory' (a nil value)
stack traceback:
	[string "sentenceMemory[{{start_row, end_row}}]:copy(s..."]:1: in main chunk
	[C]: in function 'xpcall'
	/home/francisco/torch/install/share/lua/5.1/itorch/main.lua:210: in function </home/francisco/torch/install/share/lua/5.1/itorch/main.lua:174>
	/home/francisco/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	...francisco/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	...francisco/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	...francisco/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/home/francisco/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x00405d50: 

In [81]:
predSummaryMemory[{{start_row, end_row}}]:copy(totalPredsummary)
print()

Columns 1 to 26
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0 

 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  

0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0

  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0 

 0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  

...

 0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  

0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0

  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0 

 0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  

0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0

In [ ]:

-- Now that we've stored our memory, we can build the summary to evaluate our action
predsummary = buildPredsummaryFast(qActions[i], sentences[i], SELECT)
totalPredsummary = buildTotalSummaryFast(predsummary, totalPredsummary, usecuda)

if i < n_s then
    sentencetp1Memory[{{start_row, end_row}}]:copy(sentences[i + 1])
    predSummarytp1Memory[{{start_row, end_row}}]:copy(totalPredsummary)
else 
    sentencetp1Memory[{{start_row, end_row}}]:copy(Tensor(sentences[i]:size()):fill(0) )
    predSummarytp1Memory[{{start_row, end_row}}]:copy(Tensor(totalPredsummary:size()):fill(0) )
end 

qActionMemory[{{start_row, end_row}}]:copy(qActions[i])
qPredsMemory[{{start_row, end_row}}]:copy(qPreds[i])
qValuesMemory[{{start_row, end_row}}]:copy(qValues[i])

if adapt then
    regMemory[{{start_row, end_row}}]:copy(regPreds[i])
end

for j = 1, n do
    recall, prec, f1 = rougeScores( Tokenize(totalPredsummary[j]:totable()),
                                    qTokens[j]
        )
    rougue_scores[i][j]:fill(f1)
end

if i == n_s then 
    rouguef1[epoch] = rougue_scores[i]:mean()
end 

if i == 1 then
    -- Calculating change in rougue f1
    rewards[i]:copy(rougue_scores[i])
else 
    rewards[i]:copy(rougue_scores[i] - rougue_scores[i-1])
end
rewardMemory[{{start_row, end_row}}]:copy(rewards[i])